In [1]:
from langchain_experimental.text_splitter import SemanticChunker
from langchain_text_splitters import RecursiveCharacterTextSplitter

from sklearn.metrics.pairwise import cosine_similarity
from typing import List, Dict, Any
from langchain_community.vectorstores import FAISS
from langchain_core.documents import Document
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_text_splitters import TokenTextSplitter
from langchain_core.output_parsers import StrOutputParser
import pyarrow.parquet
import json
import requests
import numpy as np
import pandas as pd
from time import sleep
import time
import re
import os
from langchain_ollama import OllamaLLM
from operator import itemgetter

In [2]:
from langchain_core.prompts import ChatPromptTemplate

In [3]:
import os
os.environ['LANGCHAIN_TRACING_V2'] = 'true'

In [4]:
model_name = "sentence-transformers/paraphrase-multilingual-mpnet-base-v2"
embeddings = HuggingFaceEmbeddings(model_name=model_name);

C:\Users\User\AppData\Local\Temp\ipykernel_13108\4184572461.py:2: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the `langchain-huggingface package and should be used instead. To use it run `pip install -U `langchain-huggingface` and import as `from `langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(model_name=model_name);


In [11]:
df = pd.read_csv('hh_vacancies_data_final.csv')
df.head()

vacancy_id                                       vacancy_name  \
0   127757615                              Junior Data Scientist   
1   127757227  Ведущий специалист отдела математического моде...   
2   127592071                                     Data Scientist   
3   127117611                                    Аналитик данных   
4   127117612                                    Аналитик данных   

         city_name                                          rag_chunk  \
0  Нижний Новгород  Вакансия: Junior Data Scientist. Город:  Нижни...   
1           Москва  Вакансия: Ведущий специалист отдела математиче...   
2      Новосибирск  Вакансия: Data Scientist. Город:  Новосибирск....   
3  Нижний Новгород  Вакансия: Аналитик данных. Город:  Нижний Новг...   
4           Самара  Вакансия: Аналитик данных. Город:  Самара. Опы...   

                                 description_cleaned  
0  1221systems аккредитованная it_компания специа...  
1  предлагаем стабильность компания финансовом ры...  
2  предлагаем официальное трудоустройство тд бела...  
3  тебе нравятся крутые амбициозные задачи мечтае...  
4  тебе нравятся крутые амбициозные задачи мечтае...

In [13]:
def create_general_chunks(row: pd.Series, splitter: Any, embeddings_model=None, use_semantic: bool = False) -> List[Dict[str, Any]]:

    # 1. Извлечение необходимых данных
    description_text = row['description_cleaned']  
    vacancy_name = row['vacancy_name']
    city_name = row['city_name']
    rag_chunk_text = row['rag_chunk']
    vacancy_id = row['vacancy_id']

    general_chunks_list: List[Dict[str, Any]] = []


    if pd.notna(description_text) and description_text.strip():
          # Используем обычное чанкование (оригинальный код)
          from langchain_core.documents import Document
        
          if hasattr(splitter, "create_documents"):
              chunks_description = splitter.create_documents([description_text])
          else:
              # Для SemanticChunker
              chunks = splitter.split_text(description_text)
              from langchain_core.documents import Document
              chunks_description = [Document(page_content=ch) for ch in chunks]

          for i, chunk in enumerate(chunks_description):
              chunk_text = chunk.page_content.strip()
              final_rag_chunk_detail = (chunk_text)

              general_chunks_list.append({
                  'vacancy_id': vacancy_id,
                  'vacancy_name': vacancy_name,
                  'city_name': city_name,
                  'rag_chunk': rag_chunk_text,
                  'full_description': final_rag_chunk_detail,
              })

    return general_chunks_list

In [268]:
def df_to_langchain_documents(df):
    """Преобразует DataFrame чанков в список объектов LangChain Document."""
    documents = []
    for index, row in df.iterrows():
        documents.append(
            Document(
                page_content=row['rag_chunk'],
                metadata={
                    "vacancy_id": row['vacancy_id'],
                    'city_name': row['city_name'],
                    'vacancy_name': row['vacancy_name']
                }
            )
        )
    return documents

## Базовый случай RECURSIVE CHUNKING

In [271]:
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=800,
    chunk_overlap=100
)

In [273]:
all_general_chunks_recursive = []
for index, row in df.iterrows():
    #  Вызываем нашу функцию для получения списка чанков из одной строки
    chunks_for_row = create_general_chunks(row, splitter=text_splitter)
    all_general_chunks_recursive.extend(chunks_for_row)

In [275]:
len(all_general_chunks_recursive)

2547

In [277]:
all_general_chunks_recursive

[{'vacancy_id': 127757615,
  'vacancy_name': 'Junior Data Scientist',
  'city_name': 'Нижний Новгород',
  'rag_chunk': 'Вакансия: Junior Data Scientist. Город:  Нижний Новгород. Опыт: От 1 года до 3 лет. График: Удаленная работа. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: проектный опыт работы временными рядами рядами регрессии года. владение python sql. навыки работы sklearn.... Обязанности: Time Series Forecasting (ритейл: прогноз продаж, прогноз количества заказов). Анализировать и визуализировать данные, выявлять закономерности, представлять результаты. Предлагать и проводить...',
  'full_description': '1221systems аккредитованная it_компания специализирующаяся разработке it_решений бизнеса розничной оптовой торговли. наша компания выполняет разработку it_продуктов группы компании quot сладкая жизнь quot одного крупнейших дистрибьюторов продуктов питания россии. данный момент находимся поиске data scientist проекты разработке корпо

In [279]:
df_general_chunks_recursive = pd.DataFrame(all_general_chunks_recursive)

In [281]:
#  База для РЕКУРСИВНОГО чанкования 
recursive_docs = df_to_langchain_documents(df_general_chunks_recursive)
db_recursive = FAISS.from_documents(recursive_docs, embeddings)

In [283]:
recursive_docs

[Document(metadata={'vacancy_id': 127757615, 'city_name': 'Нижний Новгород', 'vacancy_name': 'Junior Data Scientist'}, page_content='Вакансия: Junior Data Scientist. Город:  Нижний Новгород. Опыт: От 1 года до 3 лет. График: Удаленная работа. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: проектный опыт работы временными рядами рядами регрессии года. владение python sql. навыки работы sklearn.... Обязанности: Time Series Forecasting (ритейл: прогноз продаж, прогноз количества заказов). Анализировать и визуализировать данные, выявлять закономерности, представлять результаты. Предлагать и проводить...'),
 Document(metadata={'vacancy_id': 127757615, 'city_name': 'Нижний Новгород', 'vacancy_name': 'Junior Data Scientist'}, page_content='Вакансия: Junior Data Scientist. Город:  Нижний Новгород. Опыт: От 1 года до 3 лет. График: Удаленная работа. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: проект

In [285]:
index

707

In [287]:
retriever = db_recursive.as_retriever(search_kwargs={"k": 4})

llm = OllamaLLM(model="llama3", temperature=0)

system_template = (
   "Ты — HR-помощник, специалист по подбору персонала.\n\n"
        "Инструкции:\n"
        "1. Отвечай ТОЛЬКО на основе предоставленного контекста\n"
        "2. Всегда структурируй ответ на русском языке\n"
        "3. ВСЕГДА указывай источник вакансии [Источник: ID]\n"
        "4. Если информации недостаточно - прямо скажи об этом\n\n"
        "5. Указывай все подходящие вакансии с РАЗНЫМИ ID\n\n"
        "6. Особое внимание обрати на город, он должен совпадать ВСЕГДА \n"
        "Контекст: {context}\n\n"
        "Вопрос: {question}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_template),
        ("user", "{question}"), 
    ])

def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)
    
query_test = "Какие есть вакансии Data Scientist санкт петербурге?"

rag_chain_recursive = (
    {
        # Поиск контекста (вопрос -> retriever -> форматирование)
        "context": itemgetter("question") | retriever | format_docs,  
        # Сохранение исходного вопроса
        "question": itemgetter("question")
    }
    | prompt          #  Применение промпта к контексту и вопросу
    | llm             #  Передача в модель llm
    | StrOutputParser() #  Получение ответа в виде строки
)

rag_chain_recursive.invoke({"question": query_test})

'Вакансии Data Scientist middle в Санкт-Петербурге:\n\n* [Источник: ID 12345] - компания "IT-Company" ищет кандидата с опытом работы от 1 года до 3 лет, наличие реализованных решений и репозитория проектами. Минимальная зарплата не указана.\n* [Источник: ID 67890] - компания "DataLab" ищет кандидата с опытом работы от 1 года до 3 лет, наличие реализованных решений и репозитория проектами. Минимальная зарплата не указана.\n* [Источник: ID 34567] - компания "Analytics Inc." ищет кандидата с опытом работы от 1 года до 3 лет, наличие реализованных решений и репозитория проектами. Минимальная зарплата не указана.\n\nВсего найдено 3 вакансии Data Scientist middle в Санкт-Петербурге.'

# Multi Query

In [44]:
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=300,
    chunk_overlap=50
)

Multi_Query_chunks = []
for index, row in df.iterrows():
  
    chunks_for_row = create_general_chunks(row, splitter=text_splitter)
    #  Добавляем все чанки из текущей строки в общий список
    Multi_Query_chunks.extend(chunks_for_row)

df_general_chunks_recursive = pd.DataFrame(Multi_Query_chunks)

recursive_docs = df_to_langchain_documents(df_general_chunks_recursive)
db_recursive = FAISS.from_documents(recursive_docs, embeddings)

In [46]:
from langchain_core.load import dumps, loads

In [64]:
retriever = db_recursive.as_retriever()

llm = OllamaLLM(model="llama3", temperature=0)


template = (
    "Ты — HR-помощник, специалист по подбору персонала.  \n\n"
    "Твоя задача - сгенерировать РОВНО ПЯТЬ различных версий заданного пользователем вопроса на русском языке для извлечения соответствующих документов из векторной базы данных.\n"
    "Инструкции:\n"
    "1. Структурируй ответ на русском языке \n"
    "2. Особое внимание обрати на город, он должен совпадать ВСЕГДА с городом, который указал пользователь \n"
    "3. ИСКЛЮЧИ пустые запросы(query)"
    "4. Название вакансии не всегда должно совпадать идеально"
    "Вопрос: {question}" )


prompt = ChatPromptTemplate.from_template(template)

generate_queries = (
    prompt 
    | llm
    | StrOutputParser() 
    | (lambda x: [q.strip() for q in x.split("\n") if q.strip()])
)

def get_unique_union(documents: list[list]):
    """ Unique union of retrieved docs """
   
    flattened_docs = [dumps(doc) for sublist in documents for doc in sublist]
 
    unique_docs = list(set(flattened_docs))

    return [loads(doc) for doc in unique_docs]

question = "Какие есть вакансии Data Scientist Санкт Петербурге?"
retrieval_chain = generate_queries | retriever.map() | get_unique_union
docs = retrieval_chain.invoke({"question":question})
len(docs)

16

Довольно мало вакансий удаётся извлечь. В основном выпадают разные чанки одной и той же вакансии. Итого из нескольких десятков более менее подходящих вакансий пользователь получает 2-4. Возможно стоит исключить description_cleaned, и хранить в базе данных только город, название вакансии и краткое описание

In [71]:
# RAG
template = (
        "Ты — HR-помощник, специалист по подбору персонала.\n\n"
        "Инструкции:\n"
        "1. Отвечай ТОЛЬКО на основе предоставленного контекста\n"
        "2. ВСЕГДА  структурируй ответ на русском языке\n"
        "3. ВСЕГДА указывай источник вакансии [Источник: ID]\n"
        "4. Указывай ВСЕ подходящие вакансии с РАЗНЫМИ ID\n\n"
        "5. Особое внимание обрати на город, он должен совпадать ВСЕГДА \n"
        
        "Контекст: {context}\n\n"
        "Вопрос: {question}"
)
prompt = ChatPromptTemplate.from_template(template)

final_rag_chain = (
    {"context": retrieval_chain, 
     "question": itemgetter("question")} 
    | prompt
    | llm
    | StrOutputParser()
)

final_rag_chain.invoke({"question":question})

'Вакансии Data Scientist в Санкт-Петербурге:\n\n* Вакансия: Data Scientist middle. [Источник: 127698149, 126731632, 127704659, 35e816f7-0a0d-4f31-87f6-2d6af205d849]\n\t+ Опыт: От 1 года до 3 лет\n\t+ График: Полный день\n\t+ Занятость: Полная занятость\n\t+ Минимальная зарплата: 0.0, Максимальная зарплата: 0.0\n\t+ Требования: опыт работы 2х лет области data science, наличие реализованных внедренных решений, наличие репозитория проектами\n\t+ Обязанности: Разработка кода для формирования витрин данных, отработка гипотез и поиск оптимальной модели, построение интерпретируемых моделей, внедрение модели в промышленную среду\n\n* Вакансия: Data Scientist. [Источник: 127704659, e8ed1e20-4975-43a0-aa5e-e86edea7bdd0, b19bebcd-c407-4b15-b8d5-3c6bcf75a63c]\n\t+ Опыт: От 3 до 6 лет\n\t+ График: Полный день\n\t+ Занятость: Полная занятость\n\t+ Минимальная зарплата: 0.0, Максимальная зарплата: 0.0\n\t+ Требования: опыт 3_х лет качестве data scientist, уверенные знания математики статистики, полно

## Semantic chunking

In [75]:
embeddings_semantic = HuggingFaceEmbeddings(
    model_name="sentence-transformers/paraphrase-MiniLM-L3-v2"
)

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/629 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/314 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [76]:
# threshold — чувствительность: меньшее значение = больше чанков
semantic_chunker = SemanticChunker(embeddings_semantic, breakpoint_threshold_type="percentile", breakpoint_threshold_amount=85)

In [77]:
all_general_chunks_semantic = []
for index, row in df.iterrows():
    chunks_for_row = create_general_chunks(row, splitter=semantic_chunker)
    all_general_chunks_semantic.extend(chunks_for_row)

In [78]:
len(all_general_chunks_semantic)

2331

In [79]:
df_general_chunks_semantic = pd.DataFrame(all_general_chunks_recursive)

In [80]:
# База для semantic чанкования 
semantic_docs = df_to_langchain_documents(df_general_chunks_semantic)
db_semantic = FAISS.from_documents(semantic_docs, embeddings)

In [81]:
retriever = db_semantic.as_retriever(search_kwargs={"k": 4})

llm = OllamaLLM(model="llama3", temperature=0)

system_template = (
   "Ты — HR-помощник, специалист по подбору персонала.\n\n"
        "Инструкции:\n"
        "1. Отвечай ТОЛЬКО на основе предоставленного контекста\n"
        "2. Структурируй ответ на русском языке\n"
        "3. ВСЕГДА указывай источники в формате [Источник: ID_вакансии]\n"
        "4. Если информации недостаточно - прямо скажи об этом\n\n"
        "5. Особое внимание обрати на город, он должен совпадать ВСЕГДА \n"
        "Контекст: {context}\n\n"
        "Вопрос: {question}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_template),
        ("user", "{question}"), 
    ])


def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)
    
query_test = "Какие есть вакансии Data Scientist санкт петербурге?"


rag_chain_semantic = (
    {
        
        "context": itemgetter("question") | retriever | format_docs,  
        
        "question": itemgetter("question")
    }
    | prompt         
    | llm             
    | StrOutputParser() 
)

rag_chain_semantic.invoke({"question": query_test})

'Вакансии Data Scientist middle в Санкт-Петербурге:\n\n* Опыт работы: от 1 года до 3 лет\n* График: полный день\n* Занятость: полная занятость\n* Минимальная зарплата: не указана\n* Максимальная зарплата: не указана\n* Требования:\n\t+ Опыт работы 2х лет в области data science\n\t+ Наличие реализованных внедренных решений\n\t+ Наличие репозитория проектами\n* Обязанности:\n\t+ Разработка кода для формирования витрин данных\n\t+ Отработка гипотез и поиск оптимальной модели\n\t+ Построение интерпретируемых моделей\n\t+ Внедрение модели в промышленную среду\n\nИсточник: [Вакансия 1](ID_вакансии), [Вакансия 2](ID_вакансии), [Вакансия 3](ID_вакансии)'

### Кардинально изменю подход т.к не совсем целесообразно брать полные описания вакансий и делить их на чанки для поиска по базе данных. Буду брать только rag_chunk для поиска в базе данных

продублирую функции:

In [205]:
def df_to_langchain_documents(df):
    """Преобразует DataFrame чанков в список объектов LangChain Document."""
    documents = []
    for index, row in df.iterrows():
       
        documents.append(
            Document(
                page_content=row['rag_chunk'],
                metadata={
                    "vacancy_id": row['vacancy_id']
                }
            )
        )
    return documents

In [120]:
id_to_full = df.set_index('vacancy_id')['description_cleaned'].to_dict()

In [86]:
df_new = df.drop('description_cleaned', axis=1)
df_new.head()

vacancy_id                                       vacancy_name  \
0   127757615                              Junior Data Scientist   
1   127757227  Ведущий специалист отдела математического моде...   
2   127592071                                     Data Scientist   
3   127117611                                    Аналитик данных   
4   127117612                                    Аналитик данных   

         city_name                                          rag_chunk  
0  Нижний Новгород  Вакансия: Junior Data Scientist. Город:  Нижни...  
1           Москва  Вакансия: Ведущий специалист отдела математиче...  
2      Новосибирск  Вакансия: Data Scientist. Город:  Новосибирск....  
3  Нижний Новгород  Вакансия: Аналитик данных. Город:  Нижний Новг...  
4           Самара  Вакансия: Аналитик данных. Город:  Самара. Опы...

In [87]:
all_general_chunks_simple = df_new.to_dict(orient='records')

In [309]:
all_general_chunks_simple

[{'vacancy_id': 127757615,
  'vacancy_name': 'Junior Data Scientist',
  'city_name': 'Нижний Новгород',
  'rag_chunk': 'Вакансия: Junior Data Scientist. Город:  Нижний Новгород. Опыт: От 1 года до 3 лет. График: Удаленная работа. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: проектный опыт работы временными рядами рядами регрессии года. владение python sql. навыки работы sklearn.... Обязанности: Time Series Forecasting (ритейл: прогноз продаж, прогноз количества заказов). Анализировать и визуализировать данные, выявлять закономерности, представлять результаты. Предлагать и проводить...'},
 {'vacancy_id': 127757227,
  'vacancy_name': 'Ведущий специалист отдела математического моделирования/Data Scientist',
  'city_name': 'Москва',
  'rag_chunk': 'Вакансия: Ведущий специалист отдела математического моделирования/Data Scientist. Город:  Москва. Опыт: От 1 года до 3 лет. График: Удаленная работа. Занятость: Полная занятость. Минимальная зарпл

In [311]:
df_general_chunks_simple = pd.DataFrame(all_general_chunks_simple)

In [313]:
simple_docs = df_to_langchain_documents(df_new)
db_simple = FAISS.from_documents(simple_docs, embeddings)

In [323]:
db_simple.save_local("faiss_index_final")

In [314]:
retriever = db_simple.as_retriever(search_kwargs={"k": 8})

# LLM
llm = OllamaLLM(model="llama3", temperature=0)

system_template = (
   "Ты — HR-помощник, специалист по подбору персонала.\n\n"
        "Инструкции:\n"
        "1. Отвечай ТОЛЬКО на основе предоставленного контекста\n"
        "2. Структурируй ответ на русском языке\n"
        "3. ВСЕГДА указывай источники в формате [Источник: ID_вакансии]\n"
        "4. Если информации недостаточно - прямо скажи об этом\n\n"
        "Контекст: {context}\n\n"
        "Вопрос: {question}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_template),
        ("user", "{question}"), 
    ])


def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)
    
def get_full_descriptions(vacancy_ids, id_to_full_map):
    return {vid: id_to_full_map.get(vid, "Полное описание недоступно") for vid in vacancy_ids}

    
query_test = "Какие есть вакансии Data Scientist санкт петербурге? "


rag_chain_simple = (
    {
       
        "context": itemgetter("question") | retriever | format_docs,  
       
        "question": itemgetter("question")
    }
    | prompt         
    | llm            
    | StrOutputParser() 
)



In [315]:

docs = retriever.invoke(query_test)
retrieved_ids = [d.metadata.get('vacancy_id') for d in docs]

In [316]:
full_descriptions_for_found = {vid: id_to_full.get(vid, "Полное описание недоступно") for vid in retrieved_ids}

In [317]:
# итоговый объект/печать (пример)
result = {
    "answer": rag_answer,                 
    "retrieved_ids": retrieved_ids,       # список найденных id
    "full_descriptions": full_descriptions_for_found 
}

# Пример вывода в консоль
print(result["answer"])
for vid, full in result["full_descriptions"].items():
    print(f"\n[Источник: id {vid}]\n{full}\n")

Вакансии Data Scientist в Санкт-Петербурге:

* Вакансия: Data Scientist middle. Город: Санкт-Петербург. Опыт: От 1 года до 3 лет. График: Полный день. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: опыт работы 2х лет области data science наличие реализованных внедренных решений наличие репозитория проектами. Обязанности: Разработка кода для формирования витрин данных. Отработка гипотез и поиск оптимальной модели. Построение интерпретируемых моделей. Внедрение модели в промышленную среду.
* Вакансия: Data Scientist. Город: Санкт-Петербург. Опыт: От 3 до 6 лет. График: Полный день. Занятость: Полная занятость. Минимальная зарплата: 0.0.Максимальная зарплата: 0.0.Требования: опыт 3_х лет качестве data scientist. уверенные знания математики статистики. полное понимание владение основными семействами алгоритмов.... Обязанности: Генерация и проверка гипотез использования ML-подходов в текущих бизнес-кейсах, поиск новых кейсов. RnD-активности в т